In [1]:
import os
import pandas as pd
from dotenv import load_dotenv
import alpaca_trade_api as tradeapi
import datetime
import numpy as np
import yfinance as yf
import hvplot.pandas

In [2]:
def sharpe_ratio(df, risk_free=0, periodicity=252):
    # convert anuualized risk free rate into appropriate value
    risk_free = (1+risk_free)**(1/periodicity)-1
    excess_return = df.mean() - risk_free
    calculated_sharpe = (excess_return/df.std())*np.sqrt(periodicity)
    return calculated_sharpe

In [3]:
def retrieve_yahoo_data(ticker = 'spy', start_date = '2007-07-01', end_date = '2020-12-31'):
    try:
        yahoo_data = yf.Ticker(ticker)
        print(f"Ticker is {ticker}")
        price_df = yahoo_data.history(start=start_date, end=end_date).Close.pct_change()
        price_df.name = ticker
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [4]:
def target_downside_deviation(df, minimum_acceptable_return = 0, periodicity=252):
    df_diff = df - minimum_acceptable_return
    df_positive_excess_return = np.where(df_diff < 0, df_diff, 0)
    calculated_target_downside_deviation = np.sqrt(np.nanmean(df_positive_excess_return ** 2))
    return calculated_target_downside_deviation

In [5]:
def sortino_ratio(df, risk_free = 0, periodicity = 252, include_risk_free_in_volatility = False):
    risk_free = (1 + risk_free) ** (1/periodicity) - 1
    df_mean = np.nanmean(df) - risk_free
    if include_risk_free_in_volatility == True:
        minimum_acceptable_return = risk_free
    else:
        minimum_acceptable_return = 0
    calculated_target_downside_deviation = target_downside_deviation(df,
                                                                     minimum_acceptable_return = minimum_acceptable_return)
    df_sortino = (df_mean/calculated_target_downside_deviation) * np.sqrt(periodicity)
    return df_sortino

In [6]:
def annualized_return(df, periodicity = 252):
    difference_in_years = len(df)/periodicity
    start_net_asset_value = 1.0
    cumprod_return = np.nancumprod(df + start_net_asset_value)
    end_net_asset_value = cumprod_return[-1]
    annual_return = end_net_asset_value ** (1 / difference_in_years) - 1
    return annual_return

In [7]:
def max_dd(df, return_data = False):
    """df - asset return series, e.g. returns based on daily close prices of asset
    return_data - boolean value to determine if drawdown values over the return data time period should be return, instead of max DD"""
    # convert return series to numpy array (in case Pandas series is provided)
    df = np.asarray(df)
    # calculate cumulative returns
    start_NAV = 1
    r = np.nancumprod(df+start_NAV)
    # calculate cumulative max returns (i.e. keep track of peak cumulative return up to that point in time, despite actual cumulative return at that point in time)
    peak_r = np.maximum.accumulate(r)
    # determine drawdowns relative to peak cumulative return achieved up to each point in time
    dd = (r - peak_r) / peak_r
    # return drawdown values over time period if return_data is set to True, otherwise return max drawdown which will be a positive number
    if return_data==True:
        out = dd
    else:
        out = np.abs(np.nanmin(dd))
    return out

In [8]:
def get_max_draw_down(df, return_data = False):
    start_net_asset_value = 1.0
    cumprod_return = np.nancumprod(df + start_net_asset_value)
    peak_return = np.maximum.accumulate(cumprod_return)
    draw_down = (cumprod_return - peak_return) / peak_return
    if return_data == True:
        data = draw_down
    else:
        data = np.abs(np.nanmin(draw_down))
    return data

In [9]:
def return_max_drawdown_ratio(df, risk_free = 0, periodicity = 252):
    """df - asset return series, e.g. returns based on daily close prices of asset
   risk_free - annualized risk free rate (default is assumed to be 0)
   periodicity - number of periods at desired frequency in one year
                e.g. 252 business days in 1 year (default),
                12 months in 1 year,
                52 weeks in 1 year etc."""
    # convert annualized risk free rate into appropriate value for provided frequency of asset return series (df)
    risk_free= (1 + risk_free)**(1 / periodicity) - 1
    # determine annualized return to be used in numerator of return to max drawdown (RMDD) calculation
    annual_return = annualized_return(df, periodicity = periodicity)
    # determine max drawdown to be used in the denominator of RMDD calculation
    max_draw_down = get_max_draw_down(df, return_data = False)
    return (annual_return - risk_free) / abs(max_draw_down)

In [10]:
def average_positive(ret, drop_zero = 1):
    if drop_zero > 0:
        positives = ret > 0
    else:
        positives = ret >= 0
    if positives.any():
        return np.mean(ret[positives])
    else:
        return 0.000000000000000000000000000001

In [11]:
def average_negative(ret):
    negatives = ret < 0
    if negatives.any():
        return np.mean(ret[negatives])
    else:
        return -1*0.000000000000000000000000000001

In [12]:
def win_above_replacement_portfolio(
                    new_asset,
                    replace_port,
                    risk_free_rate = 0,
                    financing_rate = 0,
                    weight_asset = 0.25,
                    weight_replace_port = 1,
                    periodicity = 252):
    """Win Above Replacement Portolio (WARP): Total score to evaluate whether any new investment improves or hurts the return to risk of your total portfolio.
    new_asset = returns of the asset you are thinking of adding to your portfolio
    replace_port = returns of your pre-existing portfolio (e.g. S&P 500 Index, 60/40 Stock-Bond Portfolio)
    risk_free_rate = Tbill rate (annualized)
    financing_rate = portfolio margin/borrowing cost (annualized) to layer new asset on top of prevailing portfolio (e.g. LIBOR + 60bps). No financing rate is reasonable for derivate overlay products.
    weight_asset = % weight you wish to overlay for the new asset on top of the previous portfolio, 25% overlay allocation is standard
    weight_replace_port = % weight of the replacement portfolio, 100% pre-existing portfolio value is standard
    periodicity = the frequency of the data you are sampling, typically 12 for monthly or 252 for trading day count"""
    # convert annualized financing rate into appropriate value for provided periodicity
    # risk_free_rate will be converted appropriately in respective Sortino and RMDD calcs
    financing_rate = (1 + financing_rate)**(1 / periodicity) - 1

    #Calculate Replacement Portfolio Sortino Ratio
    replace_port_sortino = sortino_ratio(replace_port, risk_free = risk_free_rate, periodicity = periodicity)

    #Calculate Replacement Portfolio Return to Max Drawdown
    replace_port_return_max_drawdown = return_max_drawdown_ratio(
                                                    replace_port,
                                                    risk_free = risk_free_rate,
                                                    periodicity = periodicity)

    #Calculate New Portfolio Sortino Ratio
    total_weight = weight_asset + weight_replace_port
    new_port = (new_asset - financing_rate) * (weight_asset/total_weight) + replace_port * (weight_replace_port/total_weight)
    new_port_sortino = sortino_ratio(new_port, risk_free = risk_free_rate, periodicity = periodicity)

    #Calculate New Portfolio Return to Max Drawdown
    new_port_return_max_drawdown = return_max_drawdown_ratio(new_port, risk_free = risk_free_rate, periodicity = periodicity)

    #Final WARP calculation
    WARP = (((new_port_return_max_drawdown / replace_port_return_max_drawdown) * 
              (new_port_sortino / replace_port_sortino)) ** (1/2) - 1) * 100

    return WARP

In [13]:
def warp_additive_sortino(new_asset,
                          replace_port,
                          risk_free_rate = 0,
                          financing_rate = 0,
                          weight_asset = 0.25,
                          weight_replace_port = 1,
                          periodicity = 252):
    """Win Above Replacement Portolio (WARP) Sortino +: Isolates new investment effect on total portfolio Sortino Ratio, which is a portion of the holistic CWARP score.
    new_asset = returns of the asset you are thinking of adding to your portfolio
    replace_port = returns of your pre-existing portfolio (e.g. S&P 500 Index, 60/40 Stock-Bond Portfolio)
    risk_free_rate = Tbill rate (annualized)
    financing_rate = portfolio margin/borrowing cost (annualized) to layer new asset on top of prevailing portfolio (e.g. LIBOR + 60bps). No financing rate is reasonable for derivate overlay products.
    weight_asset = % weight you wish to overlay for the new asset on top of the previous portfolio, 25% overlay allocation is standard
    weight_replace_port = % weight of the replacement portfolio, 100% pre-existing portfolio value is standard
    periodicity = the frequency of the data you are sampling, typically 12 for monthly or 252 for trading day count"""
    # convert annualized financing rate into appropriate value for provided periodicity
    # risk_free_rate will be converted appropriately in respective Sortino and RMDD calcs
    financing_rate = (1+financing_rate)**(1/periodicity)-1

    #Calculate Replacement Portfolio Sortino Ratio
    replace_port_sortino = sortino_ratio(replace_port, risk_free = risk_free_rate, periodicity = periodicity)

    #Calculate New Portfolio Sortino Ratio
    total_weight = weight_asset + weight_replace_port
    new_port = (new_asset - financing_rate)*(weight_asset/total_weight) + replace_port * (weight_replace_port/total_weight)
    new_port_sortino = sortino_ratio(new_port, risk_free = risk_free_rate, periodicity = periodicity)

    #Final calculation
    WARP_add_sortino = ((new_port_sortino/replace_port_sortino) - 1)*100

    return WARP_add_sortino

In [14]:
def warp_additive_ret_maxdd(new_asset,
                            replace_port,
                            risk_free_rate = 0,
                            financing_rate = 0,
                            weight_asset = 0.25,
                            weight_replace_port = 1,
                            periodicity = 252):
    """Win Above Replacement Portolio (WARP) Ret to Max DD +: Isolates new investment effect on total portfolio Return to MAXDD, which is a portion of the holistic CWARP score.
    new_asset = returns of the asset you are thinking of adding to your portfolio
    replace_port = returns of your pre-existing portfolio (e.g. S&P 500 Index, 60/40 Stock-Bond Portfolio)
    risk_free_rate = Tbill rate (annualized)
    financing_rate = portfolio margin/borrowing cost (annualized) to layer new asset on top of prevailing portfolio (e.g. LIBOR + 60bps). No financing rate is reasonable for derivate overlay products.
    weight_asset = % weight you wish to overlay for the new asset on top of the previous portfolio, 25% overlay allocation is standard
    weight_replace_port = % weight of the replacement portfolio, 100% pre-existing portfolio value is standard
    periodicity = the frequency of the data you are sampling, typically 12 for monthly or 252 for trading day count"""
    # convert annualized financing rate into appropriate value for provided periodicity
    # risk_free_rate will be converted appropriately in respective Sortino and RMDD calcs
    financing_rate=(1+financing_rate)**(1/periodicity)-1

    #Calculate Replacement Portfolio Return to Max Drawdown
    replace_port_return_maxdd = return_max_drawdown_ratio(replace_port,
                                                          risk_free = risk_free_rate,
                                                          periodicity = periodicity)

    #Calculate New Portfolio Return to Max Drawdown
    total_weight = weight_asset + weight_replace_port
    new_port = (new_asset-financing_rate)*(weight_asset/total_weight)+replace_port*(weight_replace_port/total_weight)
    new_port_return_maxdd = return_max_drawdown_ratio(new_port, risk_free=risk_free_rate, periodicity=periodicity)

    #Final calculation
    WARP_add_ret_maxdd = ((new_port_return_maxdd/replace_port_return_maxdd)-1)*100

    return WARP_add_ret_maxdd

In [15]:
def warp_port_return(new_asset,
                     replace_port,
                     risk_free_rate = 0,
                     financing_rate = 0,
                     weight_asset = 0.25,
                     weight_replace_port = 1,
                     periodicity = 252):
    """Win Above Replacement Portolio CWARP) Portfolio Return: Returns of the aggregate portfolio after a new asset is financed and layered on top of the replacement portfolio.
    new_asset = returns of the asset you are thinking of adding to your portfolio
    replace_port = returns of your pre-existing portfolio (e.g. S&P 500 Index, 60/40 Stock-Bond Portfolio)
    risk_free_rate = Tbill rate (annualized)
    financing_rate = portfolio margin/borrowing cost (annualized) to layer new asset on top of prevailing portfolio (e.g. LIBOR + 60bps). No financing rate is reasonable for derivate overlay products.
    weight_asset = % weight you wish to overlay for the new asset on top of the previous portfolio, 25% overlay allocation is standard
    weight_replace_port = % weight of the replacement portfolio, 100% pre-existing portfolio value is standard
    periodicity = the frequency of the data you are sampling, typically 12 for monthly or 252 for trading day count"""
    # convert annual financing based on periodicity
    financing_rate=((financing_rate+1)**(1/periodicity)-1)

    # compose new portfolio
    total_weight = weight_asset + weight_replace_port
    new_port=(new_asset-financing_rate)*(weight_asset/total_weight)+replace_port*(weight_replace_port/total_weight)

    # calculate annualized return of new portfolio and subtract risk-free rate
    out = annualized_return(new_port, periodicity=periodicity) - risk_free_rate
    return out

In [16]:
def warp_port_risk(new_asset,
                   replace_port,
                   risk_free_rate = 0,
                   financing_rate = 0,
                   weight_asset = 0.25,
                   weight_replace_port = 1,
                   periodicity = 252):
    """Win Above Replacement Portolio (WARP) Portfolio Risk: Volatility of the aggregate portfolio after a new asset is financed and layered on top of the replacement portfolio.
    new_asset = returns of the asset you are thinking of adding to your portfolio
    replace_port = returns of your pre-existing portfolio (e.g. S&P 500 Index, 60/40 Stock-Bond Portfolio)
    risk_free_rate = Tbill rate (annualized)
    financing_rate = portfolio margin/borrowing cost (annualized) to layer new asset on top of prevailing portfolio (e.g. LIBOR + 60bps). No financing rate is reasonable for derivate overlay products.
    weight_asset = % weight you wish to overlay for the new asset on top of the previous portfolio, 25% overlay allocation is standard
    weight_replace_port = % weight of the replacement portfolio, 100% pre-existing portfolio value is standard
    periodicity = the frequency of the data you are sampling, typically 12 for monthly or 252 for trading day count"""
    # convert annual financing and risk free rates based on periodicity
    financing_rate = ((financing_rate+1)**(1/periodicity)-1)
    risk_free_rate = ((risk_free_rate+1)**(1/periodicity)-1)
    # compose new portfolio
    total_weight = weight_asset + weight_replace_port
    new_port = (new_asset - financing_rate)*(weight_asset/total_weight) + replace_port*(weight_replace_port/total_weight)
    # calculated target downside deviation (TDD)
    tdd = target_downside_deviation(new_port, minimum_acceptable_return = 0)*np.sqrt(periodicity)
    return tdd

In [17]:
def warp_new_port_data(new_asset,
                       replace_port,
                       risk_free_rate = 0,
                       financing_rate = 0,
                       weight_asset = 0.25,
                       weight_replace_port = 1,
                       periodicity = 252):
    """Win Above Replacement Portolio (WARP) return stream: Return series after a new asset is financed and layered on top of the replacement portfolio.
    new_asset = returns of the asset you are thinking of adding to your portfolio
    replace_port = returns of your pre-existing portfolio (e.g. S&P 500 Index, 60/40 Stock-Bond Portfolio)
    risk_free_rate = Tbill rate
    financing_rate = portfolio margin/borrowing cost to layer new asset on top of prevailing portfolio (e.g. LIBOR + 60bps). No financing rate is reasonable for derivate overlay products.
    weight_asset = % weight you wish to overlay for the new asset on top of the previous portfolio, 25% overlay allocation is standard
    weight_replace_port = % weight of the replacement portfolio, 100% pre-existing portfolio value is standard
    periodicity = the frequency of the data you are sampling, typically 12 for monthly or 252 for trading day count"""
    # convert annual financing based on periodicity
    financing_rate=((financing_rate + 1)**(1/periodicity) - 1)
    total_weight = weight_asset + weight_replace_port
    new_port = (new_asset - financing_rate) * (weight_asset/total_weight) + replace_port * (weight_replace_port/total_weight)
    return new_port

In [36]:
ticker_list = ["qqq", "lqd", "hyg", "tlt", "ief", "shy", "gld", "slv", "efa", "eem", "iyr", "xle", "xlk", "xlf", 'GC=F', 'RPAR']
risk_free_rate = 0.0
weight_asset = 0.25
financing_rate = 0.00
weight_replacement_port = 1.00

weight_replacement_portfolio_stock = 0.6
weight_replacement_portfolio_bond  = 0.4
ticker_replacement_portfolio_stock = 'spy'
ticker_replacement_portfolio_bond  = 'ief'
start_date = '2008-01-01'
end_date = '2020-12-31'
new_ports = {}

df_stock = retrieve_yahoo_data(ticker_replacement_portfolio_stock, start_date, end_date)
df_bond = retrieve_yahoo_data(ticker_replacement_portfolio_bond, start_date, end_date)
replacement_portfolio = ((weight_replacement_portfolio_stock * df_stock) + 
                        (weight_replacement_portfolio_bond * df_bond))

risk_ret_df = pd.DataFrame(
                index = ticker_list,
                columns = ['Start Date','End Date','WARP','+Sortino','+Ret_To_MaxDD','Sharpe','Sortino','Max_DD'])
new_risk_ret_df = pd.DataFrame(
                    index = ticker_list,
                    columns = ['Return','Vol','Sharpe','Sortino','Max_DD','Ret_To_MaxDD',f'WARP_{round(100*weight_asset)}%_asset'])
ticker_data_dict = {}

for i in range(0, len(ticker_list)):
    ticker_data = retrieve_yahoo_data(ticker_list[i])
    ticker_data_dict[ticker_list[i]] = ticker_data
    risk_ret_df.loc[ticker_list[i], 'Start Date'] = min(ticker_data.index).date()
    risk_ret_df.loc[ticker_list[i], 'End Date'] = max(ticker_data.index).date()
    risk_ret_df.loc[ticker_list[i], 'WARP'] = win_above_replacement_portfolio(
                                                new_asset = ticker_data, 
                                                replace_port = replacement_portfolio,
                                                risk_free_rate = risk_free_rate,
                                                financing_rate = financing_rate,
                                                weight_asset = weight_asset,
                                                weight_replace_port = weight_replacement_port,
                                                periodicity = 252)
    risk_ret_df.loc[ticker_list[i], '+Sortino'] = warp_additive_sortino(new_asset = ticker_data, 
                                                                        replace_port = replacement_portfolio,
                                                                        risk_free_rate = risk_free_rate,
                                                                        financing_rate = financing_rate,
                                                                        weight_asset = weight_asset,
                                                                        weight_replace_port = weight_replacement_port,
                                                                        periodicity = 252)
    risk_ret_df.loc[ticker_list[i], '+Ret_To_MaxDD'] = warp_additive_ret_maxdd(
                                                            new_asset = ticker_data, 
                                                            replace_port = replacement_portfolio,
                                                            risk_free_rate = risk_free_rate,
                                                            financing_rate = financing_rate,
                                                            weight_asset = weight_asset,
                                                            weight_replace_port = weight_replacement_port,
                                                            periodicity = 252)
    risk_ret_df.loc[ticker_list[i], 'Sharpe'] = sharpe_ratio(
                                                    ticker_data,
                                                    risk_free = risk_free_rate,
                                                    periodicity = 252)
    risk_ret_df.loc[ticker_list[i], 'Sortino'] = sortino_ratio(
                                                        ticker_data,
                                                        risk_free = risk_free_rate,
                                                        periodicity = 252)
    risk_ret_df.loc[ticker_list[i], 'Max_DD'] = max_dd(ticker_data)
    
    new_risk_ret_df.loc[ticker_list[i], 'Return'] = warp_port_return(
                                                        new_asset = ticker_data,
                                                        replace_port = replacement_portfolio,
                                                        risk_free_rate = risk_free_rate,
                                                        financing_rate = financing_rate,
                                                        weight_asset = weight_asset,
                                                        weight_replace_port = weight_replacement_port,
                                                        periodicity = 252)
    new_risk_ret_df.loc[ticker_list[i], 'Vol'] = warp_port_risk(new_asset = ticker_data,
                                                                replace_port = replacement_portfolio,
                                                                risk_free_rate = risk_free_rate,
                                                                financing_rate = financing_rate,
                                                                weight_asset = weight_asset,
                                                                weight_replace_port = weight_replacement_port,
                                                                periodicity = 252)
    cnpd = warp_new_port_data(new_asset = ticker_data,
                              replace_port = replacement_portfolio,
                              risk_free_rate = risk_free_rate,
                              financing_rate = financing_rate,
                              weight_asset = weight_asset,
                              weight_replace_port = weight_replacement_port,
                              periodicity = 252)
    new_ports[ticker_list[i]] = cnpd
    new_risk_ret_df.loc[ticker_list[i], 'Sharpe'] = sharpe_ratio(cnpd.copy(),
                                                                 risk_free = risk_free_rate,
                                                                 periodicity = 252)
    new_risk_ret_df.loc[ticker_list[i], 'Sortino'] = sortino_ratio(cnpd.copy(),
                                                                   risk_free = risk_free_rate,
                                                                   periodicity = 252)
    new_risk_ret_df.loc[ticker_list[i], 'Max_DD'] = max_dd(cnpd.copy())
    new_risk_ret_df.loc[ticker_list[i], 'Ret_To_MaxDD'] = return_max_drawdown_ratio(
                                                                            cnpd.copy(),
                                                                            risk_free = risk_free_rate,
                                                                            periodicity = 252)
    new_risk_ret_df.loc[ticker_list[i], f'WARP_{round(100*weight_asset)}%_asset'] = risk_ret_df.loc[ticker_list[i],
                                                                                                     'WARP']
#    print(f"Win above replace port for {ticker_list[i]} is {win_above_replace_port_df}")

display(risk_ret_df)
display(new_risk_ret_df)

Ticker is spy
Ticker is ief
Ticker is qqq
Ticker is lqd
Ticker is hyg
Ticker is tlt
Ticker is ief
Ticker is shy
Ticker is gld
Ticker is slv
Ticker is efa
Ticker is eem
Ticker is iyr
Ticker is xle
Ticker is xlk
Ticker is xlf
Ticker is GC=F
Ticker is RPAR


Start Date    End Date       WARP    +Sortino +Ret_To_MaxDD    Sharpe  \
qqq   2007-07-02  2020-12-30   3.480137    4.711244      2.263503  0.773863   
lqd   2007-07-02  2020-12-30   9.349883    12.46134      6.324512  0.718678   
hyg   2007-07-02  2020-12-30  -5.064786   -0.172844     -9.717003  0.505721   
tlt   2007-07-02  2020-12-30  32.580725   31.523034     33.646921  0.577914   
ief   2007-07-02  2020-12-30  18.977827   20.523342      17.45213  0.820369   
shy   2007-07-02  2020-12-30   4.764816    7.434759      2.161225  1.420665   
gld   2007-07-02  2020-12-30  13.566785   12.689019     14.451388  0.501032   
slv   2007-07-02  2020-12-30  -7.087935   -6.879502       -7.2959  0.318425   
efa   2007-07-02  2020-12-30 -25.703543    -21.2132    -29.937966  0.213238   
eem   2007-07-02  2020-12-30 -24.927244  -23.071625    -26.738102  0.255426   
iyr   2007-07-02  2020-12-30  -19.89708  -16.674217     -22.99529  0.301443   
xle   2007-07-02  2020-12-30 -34.307049  -33.145277    -35.448633  0.106641   
xlk   2007-07-02  2020-12-30   1.282483    2.121691      0.450172  0.706368   
xlf   2007-07-02  2020-12-30 -28.016335  -22.219418    -33.381212  0.226557   
GC=F  2007-07-02  2020-12-31  15.997764   15.660443     16.336068   0.52396   
RPAR  2019-12-13  2020-12-30   8.045606  353.037894    -74.232061  1.224764   

       Sortino    Max_DD  
qqq    1.09689   0.53404  
lqd   1.021375  0.217621  
hyg   0.728424  0.342465  
tlt   0.838836  0.265854  
ief   1.209351  0.104014  
shy   2.187242  0.022314  
gld   0.711232   0.45555  
slv   0.435672  0.762802  
efa   0.296051  0.610373  
eem   0.367608  0.664343  
iyr   0.427255  0.705002  
xle   0.148429  0.712628  
xlk    1.00495  0.530359  
xlf   0.327147  0.822147  
GC=F  0.747675  0.443638  
RPAR  1.668971  0.198211

Return       Vol    Sharpe   Sortino    Max_DD Ret_To_MaxDD  \
qqq   0.097819  0.092932  0.785854   1.14177  0.344334     0.284081   
lqd   0.078835  0.068372  0.839852  1.226277  0.266911     0.295362   
hyg   0.077347  0.076808  0.751857  1.088514    0.3084       0.2508   
tlt     0.0833  0.060806  0.968636  1.434125   0.22437     0.371262   
ief    0.07683  0.061682  0.891289  1.314185  0.235478     0.326274   
shy   0.069673  0.063409  0.802151  1.171467  0.245502     0.283797   
gld   0.080608  0.069821  0.839122  1.228759  0.253534     0.317938   
slv   0.081228  0.087654  0.711428  1.015384  0.315416     0.257526   
efa   0.072106  0.095173   0.59614   0.85909  0.370483     0.194627   
eem    0.07408  0.101638  0.574717  0.838826     0.364     0.203516   
iyr   0.082586  0.102994  0.628079  0.908583  0.386074     0.213914   
xle   0.064301  0.104057  0.509596  0.728983  0.358585     0.179319   
xlk   0.095684  0.093624  0.764951  1.113533  0.342902     0.279044   
xlf   0.078432  0.106635  0.584695  0.848118  0.423815     0.185062   
GC=F  0.081907  0.069529  0.861108   1.26116  0.253446     0.323174   
RPAR  0.012885  0.035151   1.02927  4.939918   0.18001     0.071582   

     WARP_25%_asset  
qqq        3.480137  
lqd        9.349883  
hyg       -5.064786  
tlt       32.580725  
ief       18.977827  
shy        4.764816  
gld       13.566785  
slv       -7.087935  
efa      -25.703543  
eem      -24.927244  
iyr       -19.89708  
xle      -34.307049  
xlk        1.282483  
xlf      -28.016335  
GC=F      15.997764  
RPAR       8.045606

In [39]:
risk_ret_df.to_csv("risk_ret.csv")
new_risk_ret_df.to_csv("new_risk_ret.csv")
new_ports_df = pd.DataFrame(new_ports)
new_ports_df.to_csv("new_ports.csv")
ticker_data_df = pd.DataFrame(ticker_data_dict)
ticker_data_df.to_csv("ticker_data.csv")
new_ports

{'qqq': Date
 2007-07-02         NaN
 2007-07-03         NaN
 2007-07-05         NaN
 2007-07-06         NaN
 2007-07-09         NaN
                 ...   
 2020-12-23   -0.001243
 2020-12-24    0.003205
 2020-12-28    0.006166
 2020-12-29   -0.000790
 2020-12-30    0.000905
 Length: 3400, dtype: float64,
 'lqd': Date
 2007-07-02         NaN
 2007-07-03         NaN
 2007-07-05         NaN
 2007-07-06         NaN
 2007-07-09         NaN
                 ...   
 2020-12-23   -0.000192
 2020-12-24    0.003007
 2020-12-28    0.004281
 2020-12-29   -0.000882
 2020-12-30    0.001160
 Length: 3400, dtype: float64,
 'hyg': Date
 2007-07-02         NaN
 2007-07-03         NaN
 2007-07-05         NaN
 2007-07-06         NaN
 2007-07-09         NaN
                 ...   
 2020-12-23    0.000666
 2020-12-24    0.002737
 2020-12-28    0.004403
 2020-12-29   -0.001222
 2020-12-30    0.001312
 Length: 3400, dtype: float64,
 'tlt': Date
 2007-07-02         NaN
 2007-07-03         NaN
 2007-07-05    

In [19]:
display(new_risk_ret_df.sort_values('Vol', ascending = True).head())

Return       Vol    Sharpe   Sortino    Max_DD Ret_To_MaxDD  \
RPAR  0.012885  0.035151   1.02927  4.939918   0.18001     0.071582   
tlt     0.0833  0.060806  0.968636  1.434125   0.22437     0.371262   
ief    0.07683  0.061682  0.891289  1.314185  0.235478     0.326274   
shy   0.069673  0.063409  0.802151  1.171467  0.245502     0.283797   
lqd   0.078835  0.068372  0.839852  1.226277  0.266911     0.295362   

     WARP_25%_asset  
RPAR       8.045606  
tlt       32.580725  
ief       18.977827  
shy        4.764816  
lqd        9.349883

In [32]:
# Sort tickers based on the WARP ratio
display(risk_ret_df.sort_values('WARP', ascending = False).head())

Start Date    End Date       WARP   +Sortino +Ret_To_MaxDD    Sharpe  \
tlt   2007-07-02  2020-12-30  32.580725  31.523034     33.646921  0.577914   
ief   2007-07-02  2020-12-30  18.977827  20.523342      17.45213  0.820369   
GC=F  2007-07-02  2020-12-31  15.997764  15.660443     16.336068   0.52396   
gld   2007-07-02  2020-12-30  13.566785  12.689019     14.451388  0.501032   
lqd   2007-07-02  2020-12-30   9.349883   12.46134      6.324512  0.718678   

       Sortino    Max_DD  
tlt   0.838836  0.265854  
ief   1.209351  0.104014  
GC=F  0.747675  0.443638  
gld   0.711232   0.45555  
lqd   1.021375  0.217621

In [21]:
# Sort tickers based on the +Sortino ratio
display(risk_ret_df.sort_values('+Sortino', ascending = False).head())

Start Date    End Date       WARP    +Sortino +Ret_To_MaxDD    Sharpe  \
RPAR  2019-12-13  2020-12-30   8.045606  353.037894    -74.232061  1.224764   
tlt   2007-07-02  2020-12-30  32.580725   31.523034     33.646921  0.577914   
ief   2007-07-02  2020-12-30  18.977827   20.523342      17.45213  0.820369   
GC=F  2007-07-02  2020-12-31  15.997764   15.660443     16.336068   0.52396   
gld   2007-07-02  2020-12-30  13.566785   12.689019     14.451388  0.501032   

       Sortino    Max_DD  
RPAR  1.668971  0.198211  
tlt   0.838836  0.265854  
ief   1.209351  0.104014  
GC=F  0.747675  0.443638  
gld   0.711232   0.45555

In [22]:
# Sort tickers based on the Sharpe Ratio
risk_ret_df.sort_values('Sharpe', ascending = False).head()

Start Date    End Date       WARP    +Sortino +Ret_To_MaxDD    Sharpe  \
shy   2007-07-02  2020-12-30   4.764816    7.434759      2.161225  1.420665   
RPAR  2019-12-13  2020-12-30   8.045606  353.037894    -74.232061  1.224764   
ief   2007-07-02  2020-12-30  18.977827   20.523342      17.45213  0.820369   
qqq   2007-07-02  2020-12-30   3.480137    4.711244      2.263503  0.773863   
lqd   2007-07-02  2020-12-30   9.349883    12.46134      6.324512  0.718678   

       Sortino    Max_DD  
shy   2.187242  0.022314  
RPAR  1.668971  0.198211  
ief   1.209351  0.104014  
qqq    1.09689   0.53404  
lqd   1.021375  0.217621

In [23]:
# Sort tickers based on the Sortino Ratio
display(risk_ret_df.sort_values('Sortino', ascending = False).head())

Start Date    End Date       WARP    +Sortino +Ret_To_MaxDD    Sharpe  \
shy   2007-07-02  2020-12-30   4.764816    7.434759      2.161225  1.420665   
RPAR  2019-12-13  2020-12-30   8.045606  353.037894    -74.232061  1.224764   
ief   2007-07-02  2020-12-30  18.977827   20.523342      17.45213  0.820369   
qqq   2007-07-02  2020-12-30   3.480137    4.711244      2.263503  0.773863   
lqd   2007-07-02  2020-12-30   9.349883    12.46134      6.324512  0.718678   

       Sortino    Max_DD  
shy   2.187242  0.022314  
RPAR  1.668971  0.198211  
ief   1.209351  0.104014  
qqq    1.09689   0.53404  
lqd   1.021375  0.217621

In [24]:
cumulative_returns = {}
for ticker in ticker_list:
    cumulative_returns[ticker] = (1 + new_ports[ticker]).cumprod()
cumulative_returns['spy'] = (1 + df_stock).cumprod() 
cumulative_returns['RPAR'] = (1 + df_stock).cumprod()
    
cumulative_returns_df = pd.DataFrame(cumulative_returns)
cumulative_returns_df.tail()

qqq       lqd       hyg       tlt       ief       shy  \
Date                                                                     
2020-12-24  3.500445  2.771140  2.720166  2.930548  2.703432  2.470970   
2020-12-28  3.522029  2.783003  2.732143  2.942971  2.714697  2.481282   
2020-12-29  3.519247  2.780548  2.728806  2.939371  2.711975  2.478878   
2020-12-30  3.522432  2.783773  2.732386  2.943284  2.714775  2.481162   
2020-12-31       NaN       NaN       NaN       NaN       NaN       NaN   

                 gld       slv       efa       eem       iyr       xle  \
Date                                                                     
2020-12-24  2.830215  2.837784  2.539921  2.595901  2.902214  2.307543   
2020-12-28  2.839907  2.860695  2.554604  2.608125  2.919561  2.314214   
2020-12-29  2.839223  2.856986  2.555420  2.613379  2.911995  2.308917   
2020-12-30  2.846122  2.868221  2.558412  2.622694  2.917235  2.318232   
2020-12-31       NaN       NaN       NaN       NaN       NaN       NaN   

                 xlk       xlf      GC=F      RPAR       spy  
Date                                                          
2020-12-24  3.413141  2.755293       NaN  3.319122  3.319122  
2020-12-28  3.435029  2.769393  2.885893  3.347636  3.347636  
2020-12-29  3.428436  2.764805  2.883864  3.341250  3.341250  
2020-12-30  3.431148  2.769769  2.889923  3.346017  3.346017  
2020-12-31       NaN       NaN       NaN       NaN       NaN

In [25]:
cumulative_returns_df.hvplot.line(
    title="Cumulative Returns - Growth of initial investment of $1",
    xlabel = "Year",
    ylabel = "Cumulative Return",
    height = 500,
    width = 1000)


:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [26]:
cumulative_returns_sel_df = cumulative_returns_df[['tlt', 'gld', 'shy', 'GC=F', 'spy', 'RPAR']]
cumulative_returns_sel_df.tail()

tlt       gld       shy      GC=F       spy      RPAR
Date                                                                  
2020-12-24  2.930548  2.830215  2.470970       NaN  3.319122  3.319122
2020-12-28  2.942971  2.839907  2.481282  2.885893  3.347636  3.347636
2020-12-29  2.939371  2.839223  2.478878  2.883864  3.341250  3.341250
2020-12-30  2.943284  2.846122  2.481162  2.889923  3.346017  3.346017
2020-12-31       NaN       NaN       NaN       NaN       NaN       NaN

In [27]:
cumulative_returns_sel_df.hvplot.line(
    title="Cumulative Returns Selected - Growth of initial investment of $1",
    xlabel = "Year",
    ylabel = "Cumulative Return",
    height = 500,
    width = 1000)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [33]:
cumulative_returns_sel_df_2008_2010 = cumulative_returns_sel_df.loc['01-01-2008':'12-31-2009']
cumulative_returns_sel_df_2008_2010.hvplot.line(
    title="Cumulative Returns Selected - 2008 to 2009 - Growth of initial investment of $1",
    xlabel = "Year",
    ylabel = "Cumulative Return",
    height = 450,
    width = 900)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [29]:
cumulative_returns_sel_df_2020 = cumulative_returns_sel_df.loc['01-01-2020':'12-31-2020']
cumulative_returns_sel_df_2020.hvplot.line(
    title="Cumulative Returns Selected - 2020 - Growth of initial investment of $1",
    xlabel = "Year",
    ylabel = "Cumulative Return",
    height = 450,
    width = 900)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [30]:
cumulative_returns_2020 = {}
for ticker in ticker_list:
    cumulative_returns_2020[ticker] = (1 + new_ports[ticker].loc['01-01-2020':'12-31-2020']).cumprod()
cumulative_returns_2020['spy'] = (1 + df_stock).loc['01-01-2020':'12-31-2020'].cumprod()    
cumulative_returns_2020_df = pd.DataFrame(cumulative_returns_2020)
display(cumulative_returns_2020_df.head())
display(cumulative_returns_2020_df.tail())

qqq       lqd       hyg       tlt       ief       shy  \
Date                                                                     
2020-01-02  1.009309  1.006392  1.006811  1.008228  1.006895  1.006064   
2020-01-03  1.005950  1.005577  1.005100  1.009825  1.006734  1.004725   
2020-01-06  1.008742  1.006400  1.006389  1.010180  1.008014  1.006148   
2020-01-07  1.006888  1.004061  1.004385  1.007359  1.005901  1.004327   
2020-01-08  1.010224  1.005595  1.006385  1.007850  1.007251  1.006050   

                 gld       slv       efa       eem       iyr       xle  \
Date                                                                     
2020-01-02  1.007439  1.007528  1.007986  1.010026  1.003757  1.007768   
2020-01-03  1.008605  1.006381  1.003977  1.004764  1.003694  1.005662   
2020-01-06  1.012221  1.009072  1.006252  1.005766  1.005360  1.008722   
2020-01-07  1.011186  1.009986  1.003882  1.003811  1.001503  1.006366   
2020-01-08  1.011499  1.008991  1.006278  1.006794  1.003796  1.004873   

                 xlk       xlf      GC=F      RPAR       spy  
Date                                                          
2020-01-02  1.009722  1.007919  1.006628  1.008875  1.009352  
2020-01-03  1.005941  1.004271  1.008384  1.008236  1.001709  
2020-01-06  1.007916  1.005633  1.012096  1.009509  1.005531  
2020-01-07  1.006005  1.002504  1.010988  1.006676  1.002703  
2020-01-08  1.009979  1.005632  1.010966  1.008349  1.008047

qqq       lqd       hyg       tlt       ief       shy  \
Date                                                                     
2020-12-24  1.218575  1.152111  1.135804  1.173510  1.151657  1.135656   
2020-12-28  1.226089  1.157043  1.140805  1.178485  1.156456  1.140396   
2020-12-29  1.225120  1.156023  1.139412  1.177043  1.155297  1.139291   
2020-12-30  1.226229  1.157363  1.140907  1.178610  1.156489  1.140341   
2020-12-31       NaN       NaN       NaN       NaN       NaN       NaN   

                 gld       slv       efa       eem       iyr       xle  \
Date                                                                     
2020-12-24  1.179469  1.226535  1.142651  1.158307  1.116368  1.060636   
2020-12-28  1.183508  1.236438  1.149256  1.163761  1.123041  1.063702   
2020-12-29  1.183223  1.234835  1.149624  1.166106  1.120131  1.061267   
2020-12-30  1.186098  1.239691  1.150970  1.170262  1.122146  1.065549   
2020-12-31       NaN       NaN       NaN       NaN       NaN       NaN   

                 xlk       xlf      GC=F      RPAR       spy  
Date                                                          
2020-12-24  1.213604  1.125697       NaN  1.166041  1.167871  
2020-12-28  1.221387  1.131458  1.179727  1.171473  1.177904  
2020-12-29  1.219043  1.129583  1.178897  1.170041  1.175657  
2020-12-30  1.220007  1.131611  1.181374  1.172478  1.177335  
2020-12-31       NaN       NaN       NaN       NaN       NaN

In [31]:
cumulative_returns_2020_sel_df = cumulative_returns_2020_df[['tlt', 'gld', 'shy', 'GC=F', 'spy']]
cumulative_returns_2020_sel_df.hvplot.line(
    title="Cumulative Returns Selected - 2020 - Growth of initial investment of $1",
    xlabel = "Year",
    ylabel = "Cumulative Return",
    height = 450,
    width = 900)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)